## Hyndman Demand Classification

In [6]:
import pandas as pd
import numpy as np

df = pd.read_csv("Sales_Data.csv")

## Get Sample Data

In [7]:
unique_eans = df["EAN UPC Key"].unique()
sample_size = int(0.25 * len(unique_eans))  
sample_size = min(sample_size, len(unique_eans)) 
sample_eans = np.random.choice(unique_eans, size=sample_size, replace=False)
df_final = df[df["EAN UPC Key"].isin(sample_eans)]

In [8]:
df_final.head(5).T

163              164              165  \
Transaction Number    KB0318120075205  KB0218120091891  KB0219010096643   
EAN UPC Key            KI008421362639   KI008421362639   KI008421362639   
Retail location Key              KB03             KB02             KB02   
Promotion                Not assigned     Not assigned     Not assigned   
Posting_Date               12/16/2018       12/23/2018       01-01-2019   
Day                                16               23                1   
Month                              12               12                1   
Year                             2018             2018             2019   
YearMonth                      201812           201812           201901   
Sales Quantity                      1                1                1   
Discount Value Net                0.0              0.0              0.0   
Discount Value Gross              0.0              0.0              0.0   
Normal Sales Value              46.67            46.67            46.67   
Retail_Value_LC                  49.0             49.0             49.0   
Retail_Value                    46.67            46.67            46.67   
Tax Amount                       2.33             2.33             2.33   
Material_Group_Key          KLGNUDSPL        KLGNUDSPL        KLGNUDSPL   
Material_Group          DSN PLUSH TOY    DSN PLUSH TOY    DSN PLUSH TOY   
Material                          NaN              NaN              NaN   
Size                              NaN              NaN              NaN   
Color                             NaN              NaN              NaN   
Brand                           KLGNU            KLGNU            KLGNU   
Category                     KLGNUDS          KLGNUDS          KLGNUDS    
Season                         CONT             CONT             CONT     
Division                        KLG              KLG              KLG     
AUR                             46.67            46.67            46.67   

                                  166              167  
Transaction Number    KB0318120074255  KB0218120094881  
EAN UPC Key            KI008421362639   KI008421362639  
Retail location Key              KB03             KB02  
Promotion                Not assigned     Not assigned  
Posting_Date               12/13/2018       12/29/2018  
Day                                13               29  
Month                              12               12  
Year                             2018             2018  
YearMonth                      201812           201812  
Sales Quantity                      1                1  
Discount Value Net                0.0              0.0  
Discount Value Gross              0.0              0.0  
Normal Sales Value              46.67            46.67  
Retail_Value_LC                  49.0             49.0  
Retail_Value                    46.67            46.67  
Tax Amount                       2.33             2.33  
Material_Group_Key          KLGNUDSPL        KLGNUDSPL  
Material_Group          DSN PLUSH TOY    DSN PLUSH TOY  
Material                          NaN              NaN  
Size                              NaN              NaN  
Color                             NaN              NaN  
Brand                           KLGNU            KLGNU  
Category                     KLGNUDS          KLGNUDS   
Season                         CONT             CONT    
Division                        KLG              KLG    
AUR                             46.67            46.67

In [9]:
def hyndman_classification(df):
    df.rename(columns={"Posting_Date":"Order_Date",
                        "Sales Quantity":"Demand",
                        "EAN UPC Key":"Product_ID"},inplace=True)

    df['Order_Date'] = pd.to_datetime(df['Order_Date'],errors='coerce')

    df = df[df["Demand"]!="Quantity Ordered"]

    demand_df = df.groupby(["Product_ID","Order_Date"]).agg(Demand=("Demand","sum"))
    demand_df = demand_df.reset_index()

    cv_data = df.groupby('Product_ID').agg(Average=('Demand','mean'),
                                            Standard_Deviation=('Demand','std')).reset_index()
            
    cv_data['Coefficient_of_Variation'] = (cv_data['Standard_Deviation']/cv_data['Average'])**2

    prod_by_date= df.groupby(['Product_ID','Order_Date']).agg(count=('Product_ID','count')).reset_index()
    skus=prod_by_date.Product_ID.value_counts()

    adi_df= pd.DataFrame()

    for i in range(len(skus.index)):
        a= prod_by_date[prod_by_date['Product_ID']==skus.index[i]]
        a['Previous_Date']=a['Order_Date'].shift(1)
        adi_df=pd.concat([adi_df,a],axis=0)

    adi_df['Duration']=adi_df['Order_Date']- adi_df['Previous_Date']
    adi_df['Duration']=adi_df['Duration'].dt.days
    adi_df = adi_df.groupby('Product_ID').agg(Average_Demand_Interval = ('Duration','mean')).reset_index()


    adi_cv=pd.merge(adi_df,cv_data)

    def demand_classification(df):
        a=0
        
        if((df['Average_Demand_Interval']<=1.32) & (df['Coefficient_of_Variation']<=0.49)):
            a='Smooth'
        if((df['Average_Demand_Interval']>=1.32) & (df['Coefficient_of_Variation']>=0.49)):  
            a='Lumpy'
        if((df['Average_Demand_Interval']<1.32) & (df['Coefficient_of_Variation']>0.49)):
            a='Erratic'
        if((df['Average_Demand_Interval']>1.32) & (df['Coefficient_of_Variation']<0.49)):
            a='Intermittent'
        return a

    adi_cv['Category']=adi_cv.apply(demand_classification,axis=1)
    adi_cv = adi_cv[adi_cv["Category"]!=0]
    return adi_cv,demand_df

In [10]:
classified_demand,demand_df = hyndman_classification(df_final)

/var/folders/k9/6cfr9hk91hj0j3bw_4hxcnkh0000gn/T/ipykernel_51291/771461667.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.rename(columns={"Posting_Date":"Order_Date",
/var/folders/k9/6cfr9hk91hj0j3bw_4hxcnkh0000gn/T/ipykernel_51291/771461667.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Order_Date'] = pd.to_datetime(df['Order_Date'],errors='coerce')
/var/folders/k9/6cfr9hk91hj0j3bw_4hxcnkh0000gn/T/ipykernel_51291/771461667.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexe

In [11]:
classified_demand

Product_ID  Average_Demand_Interval   Average  Standard_Deviation  \
0       KI008421362639                 2.000000  1.000000            0.000000   
1       KI008421362653                 1.214286  1.027778            0.166667   
2       KI008421362691                 1.062500  1.070175            0.257713   
3       KI008421368778                 1.384615  1.068966            0.257881   
4      KI1000390000009                 8.833333  0.851852            0.533761   
...                ...                      ...       ...                 ...   
15860  KI9997270000001                 9.636364  1.181818            0.664499   
15861  KI9998160000002                 7.500000  1.000000            0.000000   
15862  KI9998580000002                22.000000  1.000000            0.000000   
15863  KI9999140000005                23.000000  1.043478            0.208514   
15864  KI9999160000009                21.000000  0.750000            0.707107   

       Coefficient_of_Variation      Category  
0                      0.000000  Intermittent  
1                      0.026297        Smooth  
2                      0.057991        Smooth  
3                      0.058198  Intermittent  
4                      0.392613  Intermittent  
...                         ...           ...  
15860                  0.316145  Intermittent  
15861                  0.000000  Intermittent  
15862                  0.000000  Intermittent  
15863                  0.039931  Intermittent  
15864                  0.888889         Lumpy  

[13807 rows x 6 columns]

In [12]:
classified_demand.Category.value_counts()

Category
Intermittent    11828
Lumpy            1734
Smooth            215
Erratic            30
Name: count, dtype: int64

## Demand Classification (Demand Profile)

In [13]:
import plotly.express as px

colors = ["#EB4E82", "#96F39C", "#981EF5", "#081535", "#081535"]
px.scatter(
    classified_demand,
    x='Coefficient_of_Variation',
    y='Average_Demand_Interval',
    color='Category',
    color_discrete_sequence=colors  
)

## Smooth Demand

In [119]:
fig = px.bar(demand_df[demand_df["Product_ID"]==classified_demand.query("Category=='Smooth'")["Product_ID"].unique()[1]],
 x='Order_Date', y='Demand')
fig.update_traces(marker_color='#96F39C')

## Intermittent Demand

In [69]:
fig = px.bar(demand_df[demand_df["Product_ID"]==classified_demand.query("Category=='Intermittent'")["Product_ID"].unique()[1]],
 x='Order_Date', y='Demand')
fig.update_traces(marker_color='#EB4E82') 

## Lumpy Demand

In [71]:
fig = px.bar(demand_df[demand_df["Product_ID"]==classified_demand.query("Category=='Lumpy'")["Product_ID"].unique()[1]],
 x='Order_Date', y='Demand') 
fig.update_traces(marker_color='#981EF5') 

## Erratic Demand

In [82]:
fig = px.bar(demand_df[demand_df["Product_ID"]==classified_demand.query("Category=='Erratic'")["Product_ID"].unique()[1]],
 x='Order_Date', y='Demand') 
fig.update_traces(marker_color='#081535') 